In [ ]:
import numpy as np
import scipy as sp
from cmpy import machines
from cmpy import quantum
import qutip
import itertools
from matplotlib import pyplot as plt

# Quantum Markov Chains

## Sam Loomis

## Introduction

Computational mechanics offers a way to study the computational properties of processes that occur in nature, with applications in a variety of disciplines including classical thermodynamics. For many reasons, a quantum analogue of computational mechanics is desirable. It is known that quantum representations of processes can have a lower complexity (as measured by the von Neumann information needed to specify the causal state) (Mahoney 2016). In addition, these representations highlight an ambiguity in the relative complexity of processes, depending on whether classical or quantum representations are used (Aghamohammadi 2017). Finally, as classical computational mechanics has offered insights into classical thermodynamics, a quantum computational mechanics may offer insight into the new problems introduced by quantum thermodynamics (Vinjanampathy 2016).

Classical computational mechanics rests on the $\epsilon$-machine, which classifies the histories of a process into causal states whose predictions for the future are identical, and gives the probabilities for transitions between causal states. The $q$-machine is a first step into the advantages offered by quantum mechanics, encoding these causal states in a manner that utilizes quantum state overlap, which ultimately lowers the information required for predictivity. However, there is at least one case known - in this report referred to as the "4-Monras macine" - where there exists a quantum model which has a lower complexity (Monras 2011). The formalism in which this model exists is termed the "hidden quantum Markov model" (HQMM).

In this report, we will start by reviewing the $q$-machine and the HQMM and demonstrating that $q$-machines can be embedded in the space of HQMMs. Then we will investigate in more detail a particular class of machines that includes the 4-Monras machine, as well as its generalizations fo $n$ states: the $n$-Monras machine. The 3-Monras machine will offer some interesting lessons, investigated in the last section.

## A tale of two machines
Both of the following machine classes are extensions of the $\epsilon$-machine to the quantum domain. The $\epsilon$-machine is constructed from a process $\mathrm{Pr}\left(\overleftrightarrow{X}\right)$ (represented by a probability distribution on a bi-infinite string) by identifying the causal states; i.e. sets $S=\left\{\overleftarrow{X}\right\}$ such that for any two $\overleftarrow{X}_1,\overleftarrow{X}_2\in S$, the future morphs $\mathrm{Pr}\left(\overrightarrow{X}|\overleftarrow{X}_1\right) = \mathrm{Pr}\left(\overrightarrow{X}|\overleftarrow{X}_2\right)$ are equal. The transitions between causal states are given by the symbol-labeled transition matrices $T^{(x)}_{SS'} = \mathrm{Pr}\left(S',x|S\right)$. This encodes the $\epsilon$-machine as a hidden Markov model (HMM). A HMM model is *unifilar* if $T_{SS'}^{(x)}\neq 0$ for at most one value of $S'$ when $x$ and $S$ are given. All $\epsilon$-machines are unifilar. The process is *counifilar* if $T_{SS'}^{(x)}\neq 0$ for at most one value of $S$ when $x$ and $S'$ are given. *Not* all processes are counifilar.

The concepts of Markov order and and cryptic order are relevant for this project. The Markov order $R$ is the number of symbols I need to see to know the state I'm in: *i.e.*, the smallest value of $\ell$ for which $H(S_\ell|X_{0:\ell})=0$. The cryptic order $k$ is the number of states I need to see to determine which state I'm in, if I already know the future of that state: *i.e.* the smallest value of $\ell$ for which $H(S_\ell|X_{0:\infty})=0$. $k=0$ corresponds to counifilarity. An important feature of the cryptic order is that the statistical complexity of a system, $C_\mu$, is only equal to the excess information $\mathbf{E}$ when $k=0$.

To every $\epsilon$-machine with net transition matrix $T_{SS'} = \sum_x T^{(x)}_{SS'}$, there is a left-eigenvector $\left<\pi\right|$ such that $\left<\pi\right|T = \left<\pi\right|$, called the stationary distribution. Some causal states have zero probability under this distribution and are called *transient*. The rest are *recurrent*. The recurrent portion of an $\epsilon$-machine is itself a HMM for the process in question.

### The $q$-machine
The question of using quantum mechanics to reduce the complexity of a representation can be framed in this way: is there a way of encoding information about a process such that, for a large ensemble of $N$ identical processes, Alice can transmit the causal states to Bob through a quantum medium using less information than she could classically?

The Schumacher noisy channel coding theorem states that, for an ensemble of $N$ quantum systems prepared in some state $\rho$, the most efficient code can only compress information about the ensemble into $NS(\rho)$ qubits, where $S(\rho) = \mathrm{Tr}(\rho\log_2\rho)$ is the von Neumann entropy of the state (Schumacher 1995). This makes the von Neumann entropy a good analogy for the statistical complexity of an ensemble of processes. Hypothetically, we simply must encode the causal states of a process in some way so that the analogue to the stationary distribution $\left<\pi\right|$, the stationary state $\rho$, satsifies $S(\rho) \leq C_\mu$.

This is achieved by the $q$-machine (Mahoney 2016). This encodes the causal states of a process using their future morphs. The *$q$-machine at length $L$* encodes the state $S$ in the space $\mathcal{H}_{w^L}\otimes \mathcal{H}_{\mathcal{S}}$ as

$$ \left|\eta_S(L)\right> = \sum_{w\in w^L,\ S'} \sqrt{\mathrm{Pr}(w,S'|S)}\left|w\right>\left|S'\right> $$

In this case, the orthonormal states $\left|w\right>$ correspond to words of length $L$, while the orthonormal states $\left|S'\right>$ represent the final states. The causal states $\left|\eta_S(L)\right>$ are not necessarily orthogonal (and rarely are). This utilizes quantum overlap, which reduces the von Neumann entropy. If $\left<\pi\right|$ can be represented by the probabilities $p_S$, then the state

$$
\rho(L) = \sum_S p_S\left|\eta_S(L)\right>\left<\eta_S(L)\right|
$$

satisfies $S(\rho(L))\leq C_\mu$. We define $C_q(L)=S(\rho(L))$. Two important results bear mentioning here: that $C_q(L)$ is monotonically increasing in $L$ and reaches its maximum (herafter just referred to as $C_q$) when $L=k$, and that $C_q=C_\mu$ if and only if the process is counifilar. The first of these results follows from the fact that the overlaps $\left<\eta_S(L)\right|\left.\eta_{S'}(L)\right>$, given by

$$ \left<\eta_S(L)\right|\left.\eta_{S'}(L)\right> = \sum_{w\in w^L,S''}\sqrt{\mathrm{Pr}(w,S''|S)\mathrm{Pr}(w,S'',S')}$$

is independent of $L$ when $L\geq k$.

### The hidden quantum Markov model
Another perspective on the quantization of computational mechanics starts purely from the concept of quantum measurement (Nielsen 2011). Consider a system $\mathcal{S}$ whose internal behavior is unknown, and an environment $\mathcal{E}$ that the observer is able to measure. We suppose the system to start in some state $\left|\psi\right>$ and the environment to start in some prepared state $\left|\emptyset\right>$. The system is then coupled to the environment and evolved by some unitary operator $U$. Under the assumption that the final states of the environment are represented by some set of symbols $x$, then the final coupled state can be written as

$$
U\left|\emptyset\right>\left|\psi\right> = \sum_{x} \left|x\right>\left(K_x\left|\psi\right>\right)
$$

The operator $K_x$ is the *Krauss operator* corresponding to the symbol $x$. If the environment is then measured to be in state $\left|x\right>$ - represented by the projection operator $P_x$ - then the system is in state 
$$\left|\psi'\right> = \frac{K_x\left|\psi\right>}{\sqrt{\left<\psi\right|K_x^\dagger K_x\left|\psi\right>}}$$
with probability
$$
\mathrm{Pr}(\psi',x|\psi) = \left<\psi\right|K_x^\dagger K_x\left|\psi\right>
$$
More generally, a system starting with a density matrix $\rho$ and measuring a word $w$ transforms to state
$$\rho'= \frac{K_x \rho K_x^\dagger}{\mathrm{Tr}\left(K_x\rho K_x^\dagger\right)}$$
with probability
$$
\mathrm{Pr}(\psi',x|\psi) = \mathrm{Tr}\left(K_x\rho K_x^\dagger\right)
$$
The unitarity of $U$ requires that the Krauss operators satisfy the completeness relation
$$
\sum_x K^\dagger_x K_x = 1
$$

From this perspective, we can define the quantum analogue of a hidden Markov model - the hidden quantum Markov model (HQMM) - in terms of its Krauss operators $K_x$. The stationary state of this system is given by
$$
\sum_x K_x\rho_0K_x^\dagger = \rho_0
$$
The complexity of the system is then measured as $S(\rho_0)$.

All other causal states can then be generated from the action of the Krauss operators. This is analogous the the case of the $\epsilon$-machine, in which causal states are defined by histories. An important distinction is that states are specified first in the $\epsilon$-machine, and then the transition matrices. In this formalism, the Krauss operators are primary, from which all other properties of the machine are generated - though one must specify what type of Hilbert space we embed the Krauss operators in.

### The 4-Monras machine
The 4-Monras machine, introduced in (Monras 2011), is generated in the following code:

In [ ]:
monras4 = machines.from_string("A A 0.5; A C 0.25; A D 0.25; B B 0.5; B C 0.25; B D 0.25; C C 0.5; C A 0.25; C B 0.25;  D D 0.5; D A 0.25; D B 0.25", style=4)
monras4.draw()

The 4-Monras machine is an example of a Markov chain that has a representation in terms of a HQMM which has a lower complexity than its $q$-machine: *i.e.*, $S(\rho_0) < C_q$. Its $q$-machine form can be computed in the `cmpy.quantum` package:

In [ ]:
monras4_qM = quantum.q_machine(monras4)
print "Cq = ", monras4_qM.Cq()

The HQMM representation exists in $\mathcal{H}_2$ with basis kets $\left|0\right>$ and $\left|1\right>$. It has the Krauss operators
$$
K_A = \frac{1}{\sqrt{2}}\left|0\right>\left<0\right|,\ K_B = \frac{1}{\sqrt{2}}\left|1\right>\left<1\right|,\ K_C = \frac{1}{\sqrt{2}}\left|+\right>\left<+\right|,\ K_D = \frac{1}{\sqrt{2}}\left|-\right>\left<-\right|
$$
where
$$ \left|\pm\right> = \frac{1}{\sqrt{2}}\left(\left|0\right>\pm\left|1\right>\right)$$
The states of the system are
$$\rho_0 = \frac{1}{2}\left(\left|0\right>\left<0\right|+\left|1\right>\left<1\right|\right)$$
$$\rho_A = \left|0\right>\left<0\right|,\ \rho_B = \left|1\right>\left<1\right|, \rho_C = \left|+\right>\left<+\right|,\ \rho_D = \left|-\right>\left<-\right|$$
The stationary state $\rho_0$ is the maximally mixed state, with $S(\rho_0) = 1$. Though this is the maximal value a one-qubit (*i.e.* embedded in $\mathcal{H}_2$) machine can have, it is less than the complexity of the 4-Monras process's $q$-machine.

### Every $q$-machine is a HQMM
The above representation of the 4-Monras machine as an HQMM is not unique. In this section, we show that every $q$-machine can explicitly be written in HQMM form such that the resulting complexity matches that of the $q$-machine. While the $q$-machine is defined in terms of encoding of states, this procedure utilizes that encoding and further gives the $q$-machine an active interpretation in terms of quantum measurements.

First, we take the $q$-machine of a process encoded at $L=k$. We will just refer to the resulting causal states as $\left|\eta_S\right>$, omitting the $L$. These states form a subspace of $\mathcal{H}_{w^L}\otimes\mathcal{H}_{\mathcal{S}}$ of dimension $n$, where $n$ is the number of states. We *specifically* must restrict ourselves to the $q$-machine build from the recurrent $\epsilon$-machine here in the construction of the $q$-machine. Mixed states will be represented by mixed states over these pure states. 

We desire to construct Krauss operators $K_x$ which, upon measuring a symbol $x$, transfer state $\left|\eta_{S}\right>$ to $\left|\eta_{S'}\right>$ (where $S'$ is the unique final state, guaranteed by unifilarity) with amplitude $\sqrt{\mathrm{Pr}(x,S'|S)}$. We can accomplish this with the form
$$
K_x = \sum_x \left|\eta_{S'}\right>\left<\epsilon_{S,x}\right|
$$
where $\left<\epsilon_{S,x}\right|$ is defined by
$$\left<\epsilon_{S,x}\right|\left.\eta_{T}\right> = \sqrt{\mathrm{Pr}(x,S'|S)} \delta_{ST}$$
where $\delta_{ST}$ is the Kronecker delta. This uniquely determines $\left<\epsilon_{S,x}\right|$ if and only if the $\left|\eta_S\right>$ are linearly independent. If not (which I have not ruled out yet), then they are underdefined, so a solution would still exist.

We must check that these operators are complete. This is equivalent to asking if
$$\sum_x\left<\eta_S\right| K^\dagger_x K_x\left|\eta_T\right> = \left<\eta_S\right|\left.\eta_{T}\right>$$
for all $S$ and $T$. Indeed, we can see that the left-hand side is equal to
$$ \sum_x\left<\eta_S\right| K^\dagger_x K_x\left|\eta_T\right> = \sum_{x,w\in w^L,R}\sqrt{\mathrm{Pr}(x,S'|S)\mathrm{Pr}(x,T'|T)\mathrm{Pr}(w,R|S')\mathrm{Pr}(w,R|T')} = \sum_{wx\in w^{L+1},R}\sqrt{\mathrm{Pr}(wx,R|S)\mathrm{Pr}(wx,R|T)}$$
This is just $\left<\eta_S(L+1)\right|\left.\eta_T(L+1)\right>$. By virtue of having chosen $L=k$, this means that $\sum_x\left<\eta_S\right| K^\dagger_x K_x\left|\eta_T\right> = \left<\eta_S\right|\left.\eta_{T}\right>$, and so we have completeness.

Lastly, we show that the stationary state is given by
$$\rho_0 = \sum_S p_S \left|\eta_S\right>\left<\eta_S\right|$$
where $p_S$ determine the stationary distribution $\left<\pi\right|$. We see that
$$\sum_x K_x\rho_0 K_x^\dagger = \sum_{x,S} \mathrm{Pr}(x,S'|S)p_S\left|\eta_{S'}\right>\left<\eta_{S'}\right| = \sum_{S'} p_{S'}\left|\eta_{S'}\right>\left<\eta_{S'}\right| = \rho_0$$
via the properties of the stationary distribution. Since $\rho_0$ is the same as that used for measuring compression in the $q$-machine, $S(\rho_0) = C_q$.

### A class and a method for HQMM's
Below, I define a class for HQMMs, as well as a method for constructing one in the procedure described above from an $\epsilon$-machine. These are also contained in the file `hqmm.py`.

In [ ]:
class HQMM(object):
    """
    A 'hidden quantum markov model.'
    """
    def __init__(self,krauss_ops,alphabet=None):
        self.krauss_ops = krauss_ops
        self.dim = krauss_ops[0].shape[0]
        if alphabet == None:
            self.alphabet = list(str(i) for i in range(len(krauss_ops)))
        else:
            self.alphabet = alphabet

    def stat_dist(self):
        """
        The stationary distribution.
        """
        sd = []
        # Construct matrix representing POVM
        Kmat = np.zeros([self.dim**2,self.dim**2])
        for I in range(self.dim**2):
            i,j = int(I)/int(self.dim), int(I) % int(self.dim)
            for J in range(self.dim**2):
                k,l = int(J)/int(self.dim), int(J) % int(self.dim)
                for K in self.krauss_ops:
                    Kmat[I,J] += K.data[i,k]*(K.dag().data[l,j])
        # Find eigenvectors
        Kvals, Kvecs = np.linalg.eig(Kmat)
        ind = np.where(Kvals==abs(Kvals).max())[0]
        # Put in density matrix form
        for i in ind:
            rhomat = 0
            for J in range(self.dim**2):
                j,k = int(J)/int(self.dim), int(J) % int(self.dim)
                rhomat+= Kvecs[J,i]*qutip.basis(self.dim,j)*qutip.basis(self.dim,k).dag()
            sd.append(rhomat/rhomat.tr())
        return sd

    def complexity_vn(self):
        """
        The von Neumann complexity.
        """
        stat = self.stat_dist()[0]
        return qutip.entropy_vn(stat,base=2)

def from_eM(eM):
    """
    Builds a canonical representation of the machine as a HQMM.
    """
    qM = quantum.q_machine(eM)
    n = qM.num_states
    d = np.shape(qM.q_states[0])[0]
    alphabet = list(eM.alphabet())
    a = len(alphabet)
    trans_mats, nodes = eM.labeled_transition_matrices()

    # Find orthonormal basis
    A = np.zeros([d,0])
    for eta in qM.q_states:
        A = np.concatenate((A,eta.full()),axis=1)
    O = sp.linalg.orth(A)

    # Construct states in orthonormal basis
    new_states = []
    for s in range(n):
        eta_new = 0
        eta_old = qM.q_states[s].full()[:,0]
        for t in range(n):
            eta_new += np.dot(O[:,t],eta_old)*qutip.basis(n,t)
        new_states.append(eta_new)

    # Construct Krauss operators
    krauss_ops = []
    for x in alphabet:
        T = trans_mats[x]
        K = 0
        for s in range(n):
            Trow = T[s,:]
            new_s_array = np.where(Trow != 0.0)[0]
            if (np.size(new_s_array) != 0):
                eta = new_states[s]
                other_etas = list(e for e in new_states if e != eta)
                eps = gen_orth(other_etas)
                new_s = new_s_array[0]
                new_eta = new_states[new_s]
                amp = np.sqrt(Trow[new_s])
                eps = eps/(eps*eta).full()[0][0]*amp
                K += new_eta*eps
        krauss_ops.append(K)

    # Build HQMM
    return HQMM(krauss_ops=krauss_ops, alphabet=alphabet)

# A method to generate orthonormal vectors. Uses generalization of cross product to more vectors.
def gen_orth(other_etas):
    d = len(other_etas)+1
    v = 0
    for i in range(d):
        M = qutip.basis(d,i)*qutip.basis(d,d-1).dag()
        for j in range(d-1):
            M += other_etas[j]*qutip.basis(d,j).dag()
        v += np.linalg.det(M.full())*qutip.basis(d,i)
    v = v/v.norm()
    return v.dag()

As an example, we construct the canonical HQMM corresponding to the 4-Monras machine, as well as the one-qubit representation:

In [ ]:
monras4_canonical = from_eM(monras4)

# Constructing the 4-Monras machine in one qubit
ket0 = qutip.basis(2,0)
ket1 = qutip.basis(2,1)
ketp = 1/np.sqrt(2)*ket0+1/np.sqrt(2)*ket1
ketm = 1/np.sqrt(2)*ket0-1/np.sqrt(2)*ket1
krauss_ops = []
krauss_ops.append(1/np.sqrt(2)*ket0*ket0.dag())
krauss_ops.append(1/np.sqrt(2)*ket1*ket1.dag())
krauss_ops.append(1/np.sqrt(2)*ketp*ketp.dag())
krauss_ops.append(1/np.sqrt(2)*ketm*ketm.dag())
monras4_onequbit = HQMM(krauss_ops=krauss_ops)

print "Canonical form complexity: ", monras4_canonical.complexity_vn()
print "One-qubit form compexity: ", monras4_onequbit.complexity_vn()

## Pure projective Krauss machines
A useful special case that generalizes on the 4-Monras machine is the class of *pure projective Krauss* (PPK) machines, where the Krauss operators all have the form
$$
K_S = \frac{\left|\psi_S\right>\left<\psi_S\right|}{\sqrt{\left<\psi_S\right|\left.\psi_S\right>}}
$$
where the $\left|\psi_S\right>$ are *not necessarily normalized* kets. For simplicity, here we will restrict ourselves to the case where there are three states and $\left|\psi_S\right>\in\mathcal{H}_2$. There is a natural parametrization for 3-state PPKs that we consider next.

Before we do this, we note an important general feature of PPK's - and any machine where the Krauss operators are normal. If we set $\rho_0 = \frac{1}{d}I$, where $I$ is the identity and $d$ is the dimension, then
$$
\sum_x K_x \rho_0K_x^\dagger = \frac{1}{d}\sum_x K_x K_x^\dagger=\frac{1}{d}\sum_x K_x^\dagger K_x = \frac{1}{d}I
$$
Then $\rho_0 = \frac{1}{d}I$ is the stationary distribution, and $S(\rho_0) = \log_2 d$.
### Parametrization for 3 states
The kets can be written as
$$
\left|\psi_S\right> = \alpha_S\left|0\right> + \beta_S\left|1\right>
$$
where $\left|0\right>$ and $\left|1\right>$ are an orthonormal basis on $\mathcal{H}_2$. The completeness requirement is equivalent to

$$ \vec{\alpha}^\ast \cdot\vec{\alpha} = 1$$
$$ \vec{\beta}^\ast \cdot\vec{\beta} = 1$$
$$ \vec{\beta}^\ast \cdot\vec{\alpha} = 0$$

That is, $\vec{\alpha}$ and $\vec{\beta}$ are orthonormal complex vectors. These do not, on their own, correspond to a unique machine. It can be seen that for any 2-dimensional unitary matrix $U$, the transformation $\left|\psi_S'\right> = U\left|\psi_S\right>$ preserves the transition probabilities, and hence the final machine.This corresponds to the transformation
$$\left(\begin{array}{c}
\vec{\alpha}{}'\\
\vec{\beta}{}'
\end{array}\right) = U \left(\begin{array}{c}
\vec{\alpha}\\
\vec{\beta}
\end{array}\right)$$
This is just a rotation in the complex 2-plane spanned by $\vec{\alpha}$ and $\vec{\beta}$; thus we can see that it is only the plane itself that determines the machine. In fact, this is not all. Local phase transformations of the form $\left|\psi_S'\right> = e^{i\phi_S}\left|\psi_S\right>$ also leave the transition probabilities invariant, which corresponds to 2 additional dimensions of symmetry (unitary transformations account for one already). Assuming we label the states as $S\in \{0,1,2\}$, these allow us to restrict $\vec{\alpha}$ and $\vec{\beta}$ to be real and to have $\beta_0=0$, without loss of generality. This allows us to choose $\vec{\alpha}$ and $\vec{\beta}$ as
$$
\vec{\alpha} = (\cos\theta,\sin\theta\cos\phi,\sin\theta\sin\phi)
$$
$$
\vec{\beta} = (0,\sin\phi,-\cos\theta)
$$
The resulting kets that define the Krauss operators are
$$
\left|\psi_0\right> = \cos\theta \left|0\right>
$$
$$
\left|\psi_1\right> = \sin\theta\cos\phi \left|0\right> + \sin\phi\left|1\right>
$$
$$
\left|\psi_2\right> = \sin\theta\sin\phi \left|0\right> - \cos\phi\left|1\right>
$$

The norms of these states are
$$\mathbb{P}(\psi_0\rightarrow\psi_0)=\|\psi_0\|^2 = \cos^2\theta$$

$$\mathbb{P}(\psi_1\rightarrow\psi_1)=\|\psi_1\|^2 = {1-\cos^2\theta\cos^2\phi}$$

$$\mathbb{P}(\psi_2\rightarrow\psi_2)=\|\psi_2\|^2 = {1-\cos^2\theta\sin^2\phi}$$
and the transition probabilities are given by

$$\mathbb{P}(\psi_0\rightarrow\psi_1) = \sin^2\theta\cos^2\phi$$

$$\mathbb{P}(\psi_0\rightarrow\psi_2) = \sin^2\theta\sin^2\phi$$

$$\mathbb{P}(\psi_1\rightarrow\psi_0) = \frac{\cos^2\theta\sin^2\theta\cos^2\phi}{1-\cos^2\theta\cos^2\phi}$$

$$\mathbb{P}(\psi_1\rightarrow\psi_2) = \frac{\cos^4\theta\sin^2\phi\cos^2\phi}{1-\cos^2\theta\cos^2\phi}$$

$$\mathbb{P}(\psi_1\rightarrow\psi_0) = \frac{\cos^2\theta\sin^2\theta\sin^2\phi}{1-\cos^2\theta\sin^2\phi}$$

$$\mathbb{P}(\psi_1\rightarrow\psi_2) = \frac{\cos^4\theta\sin^2\phi\cos^2\phi}{1-\cos^2\theta\sin^2\phi}$$

It should be noted that these are invariant under $\theta \rightarrow \pi-\theta$, $\phi \rightarrow 2\pi -\phi$, and $\phi\rightarrow \pi-\phi$. This indicates a discrete symmetry so that only one octant of the sphere parametrizing the system is unique. In addition, under $\phi \rightarrow \pi/2-\phi$ switches $\psi_1$ and $\psi_2$, which is an isomorphic machine so any information theoretic quantities will be invariant under this flip. In light of this, we can write things instead by shifting variables to $\theta \rightarrow \theta/2$ and $\phi\rightarrow \phi/4$. This gives the states as
$$
\left|\psi_0\right> = \cos\left(\frac{\theta}{2}\right) \left|0\right>
$$
$$
\left|\psi_1\right> = \sin\left(\frac{\theta}{2}\right)\cos\left(\frac{\phi}{4}\right) \left|0\right> + \sin\left(\frac{\phi}{4}\right)\left|1\right>
$$
$$
\left|\psi_2\right> = \sin\left(\frac{\theta}{2}\right)\sin\left(\frac{\phi}{4}\right) \left|0\right> - \cos\left(\frac{\phi}{4}\right)\left|1\right>
$$
### A class for PPK's, and some graphs
Below, we define a class for PPK's, depending on the HQMM class. The structure of PPK's allows us to extract the states and corresponding Markov chain quickly, so that the $\epsilon$- and $q$-machines can be reconstructed.

In [ ]:
class PPK(HQMM):
    """
    A 'pure projective Krauss' machine
    """
    # This is the initialization
    def __init__(self, krauss_ops=None):
        # Setting up the states and operators
        self.states = []
        self.krauss_ops = []
        for K in krauss_ops:
            E = K*K.dag()
            if (E.tr() > 0):
                self.krauss_ops.append(K)
                Enorm = E/E.tr()
                self.states.append(Enorm)
        self.num_states = len(self.states)
        self.dim = krauss_ops[0].shape[0]

        # Setting up the machines
        self.trans_probs = np.zeros([self.num_states,self.num_states])
        for i in range(self.num_states):
            for j in range(self.num_states):
                self.trans_probs[i,j] = (self.krauss_ops[j]*self.states[i]*self.krauss_ops[j].dag()).tr()
        self.markov_chain = machines.from_matrices(self.trans_probs,style=4)
        self.eM = machines.build_eM(self.markov_chain)
        self.qM = quantum.q_machine(self.eM)
    def report(self):
        print "Statistical Complexity C_mu: ", self.eM.statistical_complexity()
        print "q-Machine Complexity C_q: ", self.qM.Cq()
        print "HQMM Complexity S: ", self.complexity_vn()

Using the previously constructed Krauss operators for the 4-Monras machine, for example, we can construct the PPK and have it report the different complexities:

In [ ]:
monras4_ppk = PPK(krauss_ops=krauss_ops)
monras4_ppk.report()

We can also use the parametrization to plot out the three-state machines on a sphere:

In [ ]:
def ThreeStateMarkov(theta,phi):
    basis = list(qutip.basis(2,i) for i in range(2))
    ket = []
    ket.append(np.cos(theta/2)*basis[0])
    ket.append(np.sin(theta/2)*np.cos(phi/4)*basis[0]+np.sin(phi/4)*basis[1])
    ket.append(np.sin(theta/2)*np.sin(phi/4)*basis[0]-np.cos(phi/4)*basis[1])
    krauss_ops = list(ket[i].norm()*ket[i].unit()*ket[i].unit().dag() for i in range(3))
    ppk = PPK(krauss_ops=krauss_ops)
    return ppk

The following code generates statistics for different values of $\theta$ and $\phi$. However, it takes a long time to run.

In [ ]:
n = 50
theta, phi = np.linspace(0.001,np.pi,n,endpoint=False), np.linspace(0.001,2*np.pi,4*n,endpoint=False)
Cmu = np.zeros([len(phi),len(theta)])
hmu =  np.zeros([len(phi),len(theta)])
E =  np.zeros([len(phi),len(theta)])
Cq =  np.zeros([len(phi),len(theta)])
S =  np.zeros([len(phi),len(theta)])
for i in range(len(theta)):
    for j in range(len(phi)):
        qmc = ThreeStateMarkov(theta[i],phi[j])
        Cmu[j,i] = qmc.eM.statistical_complexity()
        E[j,i] = qmc.eM.excess_entropy()
        hmu[j,i] = qmc.eM.entropy_rate()
        Cq[j,i] = qmc.qM.Cq()
        S[j,i] = qutip.entropy_vn(qmc.stat_dm,base=2)
np.save("Cmu-3",Cmu)
np.save("E-3",E)
np.save("hmu-3",hmu)
np.save("Cq-3",Cq)
np.save("S-3",S)

Attached are files that contain the data already that you may prefer to use:

In [ ]:
Cmu = np.load("Cmu-3.npy")
E = np.load("E-3.npy")
hmu = np.load("hmu-3.npy")
Cq = np.load("Cq-3.npy")
S = np.load("S-3.npy")
n=50

We can use Mayavi to plot various quantities on the sphere. Of particular interest is $C_q$, which we can note is always below 1, which is the value of $S$ for all PPK's. This means that the three-state, one-qubit PPK's do not improve on the corresponding $q$-machine - contrary to the case with the Monras machine.

In [ ]:
# Make sphere, choose colors
theta, phi = np.linspace(0.001,np.pi,n,endpoint=False), np.linspace(0.001,2*np.pi,4*n,endpoint=False)
x, y, z = np.zeros([len(phi),len(theta)]), np.zeros([len(phi),len(theta)]), np.zeros([len(phi),len(theta)])
for i in range(len(theta)):
    for j in range(len(phi)):
        x[j,i] = np.sin(theta[i])*np.cos(phi[j])
        y[j,i] = np.sin(theta[i])*np.sin(phi[j])
        z[j,i] = np.cos(theta[i])

In [ ]:
s = Cq
# Display
mlab.figure(1, bgcolor=(1, 1, 1), fgcolor=(0, 0, 0), size=(600, 500))
mlab.mesh(x, y, z, scalars=s, colormap='RdBu')
mlab.colorbar()
mlab.view()
mlab.show()

One can also investigate how these machines are distributed on graphs comparing different information-theoretic quantities. Below I graph $C_\mu$ versus $h_\mu$, with colors representing $C_q$.

In [ ]:
ones = np.ones(n)
ones4 = np.ones(4*n)
thetamat = np.outer(theta,ones4)
phimat = np.outer(ones,phi)
plt.scatter(hmu,Cmu,c=Cq,marker="+")
plt.xlabel('Entropy rate $h_\mu$')
plt.ylabel('Complexity $C_\mu$')
plt.title('$h_\mu$ vs $C_\mu$ for 3-state Markov Chains')
cbar = plt.colorbar()
plt.show()

We can specify the machine with the minimal value of $C_q$:

In [ ]:
x = Cq
i = np.where(x == x.min())[0][0]
j = np.where(x == x.min())[1][0]
print x[i,j]
monras3 = ThreeStateMarkov(theta[j],phi[i])
monras3.markov_chain.draw()

I call this machine the "3-Monras machine" because its transition probabilities are a 3-state analogue of the 4-Monras machine.

### Dimension is not complexity
The 3-Monras machine is not in itself remarkable, but it is an extreme yet simple example of a distinction I found important. We have shown that the 3-Monras machine has a representation as a one-qubit three-state PPK, whose complexity is $S(\rho_0) = 1$. Meanwhile, the higher-dimensional canonical representation (in 3 dimensional Hilbert space) has a complexity of $S(\rho_0) = C_q \approx 0.615$. Both low dimension and low von Neumann complexity are potentially desirable things in a HQMM, and so it seems important that they are not necessarily compatible.

## Next steps


This project has featured an interesting result regarding the relationship between $q$-machines and HQMMs, as well as some exploration of some simple cases. Throughout this process some particular questions have arisen that I find of interest:
* The von Neumann entropy is a good way to measure complexity with ensembles. Are there potentially more useful measures of complexity and information in the case of individual systems, as are encountered in single-shot thermodynamics? A resource-theoretic approach to this question may be useful.
* Throughout this paper I have used the phrase "representation" for HQMMs that replicate a process. There is a potential connection to the algebraic sense of representation theory of algebras. Representation theory is at the foundation of quantum mechanics, and as we noted above the Krauss operators seem to be the fundamental part of a HQMM. Does representation theory offer any insights as to the family of HQMMs that can represent a given process?

## References
* Mahoney, J.R., Aghamohammadi C., Crutchfield J.P. "Occam’s Quantum Strop: Synchronizing and Compressing Classical Cryptic Processes via a Quantum Channel." Scientific Reports 6, Article number: 20495 (2016)
* Monras A., Beige A., Wiesner K. "Hidden Quantum Markov Models and non-adaptive read-out of many-body states." Applied Mathematical and Computational Sciences 3, 93 (2011)
* Riechers, P.M., Mahoney, J.R., Aghamohammadi C., Crutchfield J.P. "A Closed-Form Shave from Occam's Quantum Razor: Exact Results for Quantum Compression." Phys. Rev. A 93, 052317 (2016)
* Aghamohammadi C., Mahoney, J.R., Crutchfield J.P. "The Ambiguity of Simplicity." Physics Letters A, Volume 381, Issue 14, Pages 1223–1227 (2017)
* Vinjanampathy, S., Anders, J. "Quantum Thermodynamics." Contemporary Physics,Volume 57, Issue 3, Pages 1-35, Taylor & Francis, (2016)
* Schumacher, B. "Quantum coding." Phys. Rev. A, 51:2738– 2747, (1995)
* Nielsen, M.A., Chuang, I.L. "Quantum Computation and Quantum Information, 10th Anniversary Edition." Cambridge University Press New York, NY, USA (2011)